# Bulldozer ML

In [1]:
# importing important libraries
import numpy as np
import pandas as pd
from fastai.imports import *
#from fastai.structured import *
from fastai.tabular.all import *
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
import re

In [2]:
# collecting data
#df = pd.read_csv('C:\Users\Naveen Kumar\OneDrive - RxLogix\Documents\PersoMe\ML codes\Bulldozers\Train.csv')
df = pd.read_csv('C:\\Users\\Naveen Kumar\\OneDrive - RxLogix\\Documents\\PersoMe\\MLcodes\\Bulldozers\\Train.csv',
                 low_memory = False, parse_dates =['saledate'])

In [3]:
df.columns

Index(['SalesID', 'SalePrice', 'MachineID', 'ModelID', 'datasource',
       'auctioneerID', 'YearMade', 'MachineHoursCurrentMeter', 'UsageBand',
       'saledate', 'fiModelDesc', 'fiBaseModel', 'fiSecondaryDesc',
       'fiModelSeries', 'fiModelDescriptor', 'ProductSize',
       'fiProductClassDesc', 'state', 'ProductGroup', 'ProductGroupDesc',
       'Drive_System', 'Enclosure', 'Forks', 'Pad_Type', 'Ride_Control',
       'Stick', 'Transmission', 'Turbocharged', 'Blade_Extension',
       'Blade_Width', 'Enclosure_Type', 'Engine_Horsepower', 'Hydraulics',
       'Pushblock', 'Ripper', 'Scarifier', 'Tip_Control', 'Tire_Size',
       'Coupler', 'Coupler_System', 'Grouser_Tracks', 'Hydraulics_Flow',
       'Track_Type', 'Undercarriage_Pad_Width', 'Stick_Length', 'Thumb',
       'Pattern_Changer', 'Grouser_Type', 'Backhoe_Mounting', 'Blade_Type',
       'Travel_Controls', 'Differential_Type', 'Steering_Controls'],
      dtype='object')

In [5]:
df.Coupler_System.unique()

array([nan, 'None or Unspecified', 'Yes'], dtype=object)

In [7]:
df.shape

(401125, 53)

In [13]:
len(df)

401125

In [10]:
df[df['Coupler_System'] != 'Yes'].shape

(398097, 53)

In [11]:
for i in df.columns:
    if df[i].isnull().values.any():
        print(i)
        

auctioneerID
MachineHoursCurrentMeter
UsageBand
fiSecondaryDesc
fiModelSeries
fiModelDescriptor
ProductSize
Drive_System
Enclosure
Forks
Pad_Type
Ride_Control
Stick
Transmission
Turbocharged
Blade_Extension
Blade_Width
Enclosure_Type
Engine_Horsepower
Hydraulics
Pushblock
Ripper
Scarifier
Tip_Control
Tire_Size
Coupler
Coupler_System
Grouser_Tracks
Hydraulics_Flow
Track_Type
Undercarriage_Pad_Width
Stick_Length
Thumb
Pattern_Changer
Grouser_Type
Backhoe_Mounting
Blade_Type
Travel_Controls
Differential_Type
Steering_Controls


In [3]:
df.head()

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  YearMade  \
0  1139246      66000     999089     3157         121           3.0      2004   
1  1139248      57000     117657       77         121           3.0      1996   
2  1139249      10000     434808     7009         121           3.0      2001   
3  1139251      38500    1026470      332         121           3.0      2001   
4  1139253      11000    1057373    17311         121           3.0      2007   

   MachineHoursCurrentMeter UsageBand   saledate  ... Undercarriage_Pad_Width  \
0                      68.0       Low 2006-11-16  ...                     NaN   
1                    4640.0       Low 2004-03-26  ...                     NaN   
2                    2838.0      High 2004-02-26  ...                     NaN   
3                    3486.0      High 2011-05-19  ...                     NaN   
4                     722.0    Medium 2009-07-23  ...                     NaN   

  Stick_Length Thumb Pattern_Changer Grouser_Type Backhoe_Mounting Blade_Type  \
0          NaN   NaN             NaN          NaN              NaN        NaN   
1          NaN   NaN             NaN          NaN              NaN        NaN   
2          NaN   NaN             NaN          NaN              NaN        NaN   
3          NaN   NaN             NaN          NaN              NaN        NaN   
4          NaN   NaN             NaN          NaN              NaN        NaN   

  Travel_Controls Differential_Type Steering_Controls  
0             NaN          Standard      Conventional  
1             NaN          Standard      Conventional  
2             NaN               NaN               NaN  
3             NaN               NaN               NaN  
4             NaN               NaN               NaN  

[5 rows x 53 columns]

In [4]:
df.shape

(401125, 53)

In [5]:
pd.set_option('display.max_columns', None)

In [6]:
df.head()

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  YearMade  \
0  1139246      66000     999089     3157         121           3.0      2004   
1  1139248      57000     117657       77         121           3.0      1996   
2  1139249      10000     434808     7009         121           3.0      2001   
3  1139251      38500    1026470      332         121           3.0      2001   
4  1139253      11000    1057373    17311         121           3.0      2007   

   MachineHoursCurrentMeter UsageBand   saledate fiModelDesc fiBaseModel  \
0                      68.0       Low 2006-11-16        521D         521   
1                    4640.0       Low 2004-03-26      950FII         950   
2                    2838.0      High 2004-02-26         226         226   
3                    3486.0      High 2011-05-19    PC120-6E       PC120   
4                     722.0    Medium 2009-07-23        S175        S175   

  fiSecondaryDesc fiModelSeries fiModelDescriptor ProductSize  \
0               D           NaN               NaN         NaN   
1               F            II               NaN      Medium   
2             NaN           NaN               NaN         NaN   
3             NaN           -6E               NaN       Small   
4             NaN           NaN               NaN         NaN   

                                           fiProductClassDesc           state  \
0                    Wheel Loader - 110.0 to 120.0 Horsepower         Alabama   
1                    Wheel Loader - 150.0 to 175.0 Horsepower  North Carolina   
2  Skid Steer Loader - 1351.0 to 1601.0 Lb Operating Capacity        New York   
3       Hydraulic Excavator, Track - 12.0 to 14.0 Metric Tons           Texas   
4  Skid Steer Loader - 1601.0 to 1751.0 Lb Operating Capacity        New York   

  ProductGroup    ProductGroupDesc Drive_System   Enclosure  \
0           WL        Wheel Loader          NaN  EROPS w AC   
1           WL        Wheel Loader          NaN  EROPS w AC   
2          SSL  Skid Steer Loaders          NaN       OROPS   
3          TEX    Track Excavators          NaN  EROPS w AC   
4          SSL  Skid Steer Loaders          NaN       EROPS   

                 Forks Pad_Type         Ride_Control Stick Transmission  \
0  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
1  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
2  None or Unspecified      NaN                  NaN   NaN          NaN   
3                  NaN      NaN                  NaN   NaN          NaN   
4  None or Unspecified      NaN                  NaN   NaN          NaN   

  Turbocharged Blade_Extension Blade_Width Enclosure_Type Engine_Horsepower  \
0          NaN             NaN         NaN            NaN               NaN   
1          NaN             NaN         NaN            NaN               NaN   
2          NaN             NaN         NaN            NaN               NaN   
3          NaN             NaN         NaN            NaN               NaN   
4          NaN             NaN         NaN            NaN               NaN   

  Hydraulics Pushblock Ripper Scarifier Tip_Control            Tire_Size  \
0    2 Valve       NaN    NaN       NaN         NaN  None or Unspecified   
1    2 Valve       NaN    NaN       NaN         NaN                 23.5   
2  Auxiliary       NaN    NaN       NaN         NaN                  NaN   
3    2 Valve       NaN    NaN       NaN         NaN                  NaN   
4  Auxiliary       NaN    NaN       NaN         NaN                  NaN   

               Coupler       Coupler_System       Grouser_Tracks  \
0  None or Unspecified                  NaN                  NaN   
1  None or Unspecified                  NaN                  NaN   
2  None or Unspecified  None or Unspecified  None or Unspecified   
3  None or Unspecified                  NaN                  NaN   
4  None or Unspecified  None or Unspecified  None or Unspecified   

  Hydrauli

In [7]:
# Formating data to appropriate format
df_use = df.copy()

In [8]:
df_use.head()

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  YearMade  \
0  1139246      66000     999089     3157         121           3.0      2004   
1  1139248      57000     117657       77         121           3.0      1996   
2  1139249      10000     434808     7009         121           3.0      2001   
3  1139251      38500    1026470      332         121           3.0      2001   
4  1139253      11000    1057373    17311         121           3.0      2007   

   MachineHoursCurrentMeter UsageBand   saledate fiModelDesc fiBaseModel  \
0                      68.0       Low 2006-11-16        521D         521   
1                    4640.0       Low 2004-03-26      950FII         950   
2                    2838.0      High 2004-02-26         226         226   
3                    3486.0      High 2011-05-19    PC120-6E       PC120   
4                     722.0    Medium 2009-07-23        S175        S175   

  fiSecondaryDesc fiModelSeries fiModelDescriptor ProductSize  \
0               D           NaN               NaN         NaN   
1               F            II               NaN      Medium   
2             NaN           NaN               NaN         NaN   
3             NaN           -6E               NaN       Small   
4             NaN           NaN               NaN         NaN   

                                           fiProductClassDesc           state  \
0                    Wheel Loader - 110.0 to 120.0 Horsepower         Alabama   
1                    Wheel Loader - 150.0 to 175.0 Horsepower  North Carolina   
2  Skid Steer Loader - 1351.0 to 1601.0 Lb Operating Capacity        New York   
3       Hydraulic Excavator, Track - 12.0 to 14.0 Metric Tons           Texas   
4  Skid Steer Loader - 1601.0 to 1751.0 Lb Operating Capacity        New York   

  ProductGroup    ProductGroupDesc Drive_System   Enclosure  \
0           WL        Wheel Loader          NaN  EROPS w AC   
1           WL        Wheel Loader          NaN  EROPS w AC   
2          SSL  Skid Steer Loaders          NaN       OROPS   
3          TEX    Track Excavators          NaN  EROPS w AC   
4          SSL  Skid Steer Loaders          NaN       EROPS   

                 Forks Pad_Type         Ride_Control Stick Transmission  \
0  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
1  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
2  None or Unspecified      NaN                  NaN   NaN          NaN   
3                  NaN      NaN                  NaN   NaN          NaN   
4  None or Unspecified      NaN                  NaN   NaN          NaN   

  Turbocharged Blade_Extension Blade_Width Enclosure_Type Engine_Horsepower  \
0          NaN             NaN         NaN            NaN               NaN   
1          NaN             NaN         NaN            NaN               NaN   
2          NaN             NaN         NaN            NaN               NaN   
3          NaN             NaN         NaN            NaN               NaN   
4          NaN             NaN         NaN            NaN               NaN   

  Hydraulics Pushblock Ripper Scarifier Tip_Control            Tire_Size  \
0    2 Valve       NaN    NaN       NaN         NaN  None or Unspecified   
1    2 Valve       NaN    NaN       NaN         NaN                 23.5   
2  Auxiliary       NaN    NaN       NaN         NaN                  NaN   
3    2 Valve       NaN    NaN       NaN         NaN                  NaN   
4  Auxiliary       NaN    NaN       NaN         NaN                  NaN   

               Coupler       Coupler_System       Grouser_Tracks  \
0  None or Unspecified                  NaN                  NaN   
1  None or Unspecified                  NaN                  NaN   
2  None or Unspecified  None or Unspecified  None or Unspecified   
3  None or Unspecified                  NaN                  NaN   
4  None or Unspecified  None or Unspecified  None or Unspecified   

  Hydrauli

In [9]:
df_use.SalePrice = np.log(df_use.SalePrice)

In [10]:
df_use.head()

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  YearMade  \
0  1139246  11.097410     999089     3157         121           3.0      2004   
1  1139248  10.950807     117657       77         121           3.0      1996   
2  1139249   9.210340     434808     7009         121           3.0      2001   
3  1139251  10.558414    1026470      332         121           3.0      2001   
4  1139253   9.305651    1057373    17311         121           3.0      2007   

   MachineHoursCurrentMeter UsageBand   saledate fiModelDesc fiBaseModel  \
0                      68.0       Low 2006-11-16        521D         521   
1                    4640.0       Low 2004-03-26      950FII         950   
2                    2838.0      High 2004-02-26         226         226   
3                    3486.0      High 2011-05-19    PC120-6E       PC120   
4                     722.0    Medium 2009-07-23        S175        S175   

  fiSecondaryDesc fiModelSeries fiModelDescriptor ProductSize  \
0               D           NaN               NaN         NaN   
1               F            II               NaN      Medium   
2             NaN           NaN               NaN         NaN   
3             NaN           -6E               NaN       Small   
4             NaN           NaN               NaN         NaN   

                                           fiProductClassDesc           state  \
0                    Wheel Loader - 110.0 to 120.0 Horsepower         Alabama   
1                    Wheel Loader - 150.0 to 175.0 Horsepower  North Carolina   
2  Skid Steer Loader - 1351.0 to 1601.0 Lb Operating Capacity        New York   
3       Hydraulic Excavator, Track - 12.0 to 14.0 Metric Tons           Texas   
4  Skid Steer Loader - 1601.0 to 1751.0 Lb Operating Capacity        New York   

  ProductGroup    ProductGroupDesc Drive_System   Enclosure  \
0           WL        Wheel Loader          NaN  EROPS w AC   
1           WL        Wheel Loader          NaN  EROPS w AC   
2          SSL  Skid Steer Loaders          NaN       OROPS   
3          TEX    Track Excavators          NaN  EROPS w AC   
4          SSL  Skid Steer Loaders          NaN       EROPS   

                 Forks Pad_Type         Ride_Control Stick Transmission  \
0  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
1  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
2  None or Unspecified      NaN                  NaN   NaN          NaN   
3                  NaN      NaN                  NaN   NaN          NaN   
4  None or Unspecified      NaN                  NaN   NaN          NaN   

  Turbocharged Blade_Extension Blade_Width Enclosure_Type Engine_Horsepower  \
0          NaN             NaN         NaN            NaN               NaN   
1          NaN             NaN         NaN            NaN               NaN   
2          NaN             NaN         NaN            NaN               NaN   
3          NaN             NaN         NaN            NaN               NaN   
4          NaN             NaN         NaN            NaN               NaN   

  Hydraulics Pushblock Ripper Scarifier Tip_Control            Tire_Size  \
0    2 Valve       NaN    NaN       NaN         NaN  None or Unspecified   
1    2 Valve       NaN    NaN       NaN         NaN                 23.5   
2  Auxiliary       NaN    NaN       NaN         NaN                  NaN   
3    2 Valve       NaN    NaN       NaN         NaN                  NaN   
4  Auxiliary       NaN    NaN       NaN         NaN                  NaN   

               Coupler       Coupler_System       Grouser_Tracks  \
0  None or Unspecified                  NaN                  NaN   
1  None or Unspecified                  NaN                  NaN   
2  None or Unspecified  None or Unspecified  None or Unspecified   
3  None or Unspecified                  NaN                  NaN   
4  None or Unspecified  None or Unspecified  None or Unspecified   

  Hydrauli

In [11]:
df_use.dtypes

SalesID                              int64
SalePrice                          float64
MachineID                            int64
ModelID                              int64
datasource                           int64
auctioneerID                       float64
YearMade                             int64
MachineHoursCurrentMeter           float64
UsageBand                           object
saledate                    datetime64[ns]
fiModelDesc                         object
fiBaseModel                         object
fiSecondaryDesc                     object
fiModelSeries                       object
fiModelDescriptor                   object
ProductSize                         object
fiProductClassDesc                  object
state                               object
ProductGroup                        object
ProductGroupDesc                    object
Drive_System                        object
Enclosure                           object
Forks                               object
Pad_Type   

In [12]:
add_datepart(df_use, 'saledate')
df_use.saleYear.head()

0    2006
1    2004
2    2004
3    2011
4    2009
Name: saleYear, dtype: int64

In [13]:
df_use.head()

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  YearMade  \
0  1139246  11.097410     999089     3157         121           3.0      2004   
1  1139248  10.950807     117657       77         121           3.0      1996   
2  1139249   9.210340     434808     7009         121           3.0      2001   
3  1139251  10.558414    1026470      332         121           3.0      2001   
4  1139253   9.305651    1057373    17311         121           3.0      2007   

   MachineHoursCurrentMeter UsageBand fiModelDesc fiBaseModel fiSecondaryDesc  \
0                      68.0       Low        521D         521               D   
1                    4640.0       Low      950FII         950               F   
2                    2838.0      High         226         226             NaN   
3                    3486.0      High    PC120-6E       PC120             NaN   
4                     722.0    Medium        S175        S175             NaN   

  fiModelSeries fiModelDescriptor ProductSize  \
0           NaN               NaN         NaN   
1            II               NaN      Medium   
2           NaN               NaN         NaN   
3           -6E               NaN       Small   
4           NaN               NaN         NaN   

                                           fiProductClassDesc           state  \
0                    Wheel Loader - 110.0 to 120.0 Horsepower         Alabama   
1                    Wheel Loader - 150.0 to 175.0 Horsepower  North Carolina   
2  Skid Steer Loader - 1351.0 to 1601.0 Lb Operating Capacity        New York   
3       Hydraulic Excavator, Track - 12.0 to 14.0 Metric Tons           Texas   
4  Skid Steer Loader - 1601.0 to 1751.0 Lb Operating Capacity        New York   

  ProductGroup    ProductGroupDesc Drive_System   Enclosure  \
0           WL        Wheel Loader          NaN  EROPS w AC   
1           WL        Wheel Loader          NaN  EROPS w AC   
2          SSL  Skid Steer Loaders          NaN       OROPS   
3          TEX    Track Excavators          NaN  EROPS w AC   
4          SSL  Skid Steer Loaders          NaN       EROPS   

                 Forks Pad_Type         Ride_Control Stick Transmission  \
0  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
1  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
2  None or Unspecified      NaN                  NaN   NaN          NaN   
3                  NaN      NaN                  NaN   NaN          NaN   
4  None or Unspecified      NaN                  NaN   NaN          NaN   

  Turbocharged Blade_Extension Blade_Width Enclosure_Type Engine_Horsepower  \
0          NaN             NaN         NaN            NaN               NaN   
1          NaN             NaN         NaN            NaN               NaN   
2          NaN             NaN         NaN            NaN               NaN   
3          NaN             NaN         NaN            NaN               NaN   
4          NaN             NaN         NaN            NaN               NaN   

  Hydraulics Pushblock Ripper Scarifier Tip_Control            Tire_Size  \
0    2 Valve       NaN    NaN       NaN         NaN  None or Unspecified   
1    2 Valve       NaN    NaN       NaN         NaN                 23.5   
2  Auxiliary       NaN    NaN       NaN         NaN                  NaN   
3    2 Valve       NaN    NaN       NaN         NaN                  NaN   
4  Auxiliary       NaN    NaN       NaN         NaN                  NaN   

               Coupler       Coupler_System       Grouser_Tracks  \
0  None or Unspecified                  NaN                  NaN   
1  None or Unspecified                  NaN                  NaN   
2  None or Unspecified  None or Unspecified  None or Unspecified   
3  None or Unspecified                  NaN                  NaN   
4  None or Unspecified  None or Unspecified  None or Unspecified   

  Hydraulics_Flow Track_Type Undercarriage_Pad_Width Stick_Length Thumb  \
0

In [16]:
# drop model columns
df_use.drop(labels = ['fiModelDesc','fiBaseModel','fiSecondaryDesc','fiModelSeries','fiModelDescriptor','fiProductClassDesc'], axis = 1)

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  \
0       1139246  11.097410     999089     3157         121           3.0   
1       1139248  10.950807     117657       77         121           3.0   
2       1139249   9.210340     434808     7009         121           3.0   
3       1139251  10.558414    1026470      332         121           3.0   
4       1139253   9.305651    1057373    17311         121           3.0   
...         ...        ...        ...      ...         ...           ...   
401120  6333336   9.259131    1840702    21439         149           1.0   
401121  6333337   9.305651    1830472    21439         149           1.0   
401122  6333338   9.350102    1887659    21439         149           1.0   
401123  6333341   9.104980    1903570    21435         149           2.0   
401124  6333342   8.955448    1926965    21435         149           2.0   

        YearMade  MachineHoursCurrentMeter UsageBand ProductSize  \
0           2004                      68.0       Low         NaN   
1           1996                    4640.0       Low      Medium   
2           2001                    2838.0      High         NaN   
3           2001                    3486.0      High       Small   
4           2007                     722.0    Medium         NaN   
...          ...                       ...       ...         ...   
401120      2005                       NaN       NaN        Mini   
401121      2005                       NaN       NaN        Mini   
401122      2005                       NaN       NaN        Mini   
401123      2005                       NaN       NaN        Mini   
401124      2005                       NaN       NaN        Mini   

                 state ProductGroup    ProductGroupDesc Drive_System  \
0              Alabama           WL        Wheel Loader          NaN   
1       North Carolina           WL        Wheel Loader          NaN   
2             New York          SSL  Skid Steer Loaders          NaN   
3                Texas          TEX    Track Excavators          NaN   
4             New York          SSL  Skid Steer Loaders          NaN   
...                ...          ...                 ...          ...   
401120        Maryland          TEX    Track Excavators          NaN   
401121        Maryland          TEX    Track Excavators          NaN   
401122        Maryland          TEX    Track Excavators          NaN   
401123         Florida          TEX    Track Excavators          NaN   
401124         Florida          TEX    Track Excavators          NaN   

         Enclosure                Forks Pad_Type         Ride_Control Stick  \
0       EROPS w AC  None or Unspecified      NaN  None or Unspecified   NaN   
1       EROPS w AC  None or Unspecified      NaN  None or Unspecified   NaN   
2            OROPS  None or Unspecified      NaN                  NaN   NaN   
3       EROPS w AC                  NaN      NaN                  NaN   NaN   
4            EROPS  None or Unspecified      NaN                  NaN   NaN   
...            ...                  ...      ...                  ...   ...   
401120       EROPS                  NaN      NaN                  NaN   NaN   
401121       EROPS                  NaN      NaN                  NaN   NaN   
401122       EROPS                  NaN      NaN                  NaN   NaN   
401123       EROPS                  NaN      NaN                  NaN   NaN   
401124       EROPS                  NaN      NaN                  NaN   NaN   

       Transmission Turbocharged Blade_Extension Blade_Width Enclosure_Type  \
0               NaN          NaN             NaN         NaN            NaN   
1               NaN          NaN             NaN         NaN            NaN   
2               NaN          NaN             NaN         NaN            NaN   
3               NaN          NaN             NaN         NaN            NaN   
4               NaN          NaN             NaN         NaN         

In [17]:
df_use['Blade_Width'].unique()

array([nan, 'None or Unspecified', "12'", "14'", "13'", "16'", "<12'"],
      dtype=object)

In [45]:
df_use.head()

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  YearMade  \
0  1139246  11.097410     999089     3157         121           3.0      2004   
1  1139248  10.950807     117657       77         121           3.0      1996   
2  1139249   9.210340     434808     7009         121           3.0      2001   
3  1139251  10.558414    1026470      332         121           3.0      2001   
4  1139253   9.305651    1057373    17311         121           3.0      2007   

   MachineHoursCurrentMeter UsageBand fiModelDesc fiBaseModel fiSecondaryDesc  \
0                      68.0       Low        521D         521               D   
1                    4640.0       Low      950FII         950               F   
2                    2838.0      High         226         226             NaN   
3                    3486.0      High    PC120-6E       PC120             NaN   
4                     722.0    Medium        S175        S175             NaN   

  fiModelSeries fiModelDescriptor ProductSize  \
0           NaN               NaN         NaN   
1            II               NaN      Medium   
2           NaN               NaN         NaN   
3           -6E               NaN       Small   
4           NaN               NaN         NaN   

                                           fiProductClassDesc           state  \
0                    Wheel Loader - 110.0 to 120.0 Horsepower         Alabama   
1                    Wheel Loader - 150.0 to 175.0 Horsepower  North Carolina   
2  Skid Steer Loader - 1351.0 to 1601.0 Lb Operating Capacity        New York   
3       Hydraulic Excavator, Track - 12.0 to 14.0 Metric Tons           Texas   
4  Skid Steer Loader - 1601.0 to 1751.0 Lb Operating Capacity        New York   

  ProductGroup    ProductGroupDesc Drive_System   Enclosure  \
0           WL        Wheel Loader          NaN  EROPS w AC   
1           WL        Wheel Loader          NaN  EROPS w AC   
2          SSL  Skid Steer Loaders          NaN       OROPS   
3          TEX    Track Excavators          NaN  EROPS w AC   
4          SSL  Skid Steer Loaders          NaN       EROPS   

                 Forks Pad_Type         Ride_Control Stick Transmission  \
0  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
1  None or Unspecified      NaN  None or Unspecified   NaN          NaN   
2  None or Unspecified      NaN                  NaN   NaN          NaN   
3                  NaN      NaN                  NaN   NaN          NaN   
4  None or Unspecified      NaN                  NaN   NaN          NaN   

  Turbocharged Blade_Extension  Blade_Width Enclosure_Type Engine_Horsepower  \
0          NaN             NaN           13            NaN               NaN   
1          NaN             NaN           13            NaN               NaN   
2          NaN             NaN           13            NaN               NaN   
3          NaN             NaN           13            NaN               NaN   
4          NaN             NaN           13            NaN               NaN   

  Hydraulics Pushblock Ripper Scarifier Tip_Control  Tire_Size  \
0    2 Valve       NaN    NaN       NaN         NaN        NaN   
1    2 Valve       NaN    NaN       NaN         NaN       23.5   
2  Auxiliary       NaN    NaN       NaN         NaN        NaN   
3    2 Valve       NaN    NaN       NaN         NaN        NaN   
4  Auxiliary       NaN    NaN       NaN         NaN        NaN   

               Coupler       Coupler_System       Grouser_Tracks  \
0  None or Unspecified                  NaN                  NaN   
1  None or Unspecified                  NaN                  NaN   
2  None or Unspecified  None or Unspecified  None or Unspecified   
3  None or Unspecified                  NaN                  NaN   
4  None or Unspecified  None or Unspecified  None or Unspecified   

  Hydraulics_Flow Track_Type  Undercarriage_Pad_Width  Stick_Length Thumb  \
0             NaN        NaN                      NaN

In [18]:
# handle blade width
df_use['Blade_Width'].replace(to_replace = [np.nan, 'None or Unspecified', "12'", "14'", "13'", "16'", "<12'"],
                             value = [13, 13, 12, 14, 13, 16, 10], inplace =  True)

In [19]:
np.median([12,14,13,16,10])

13.0

In [20]:
#Tire_Size
df_use['Tire_Size'].unique()

array(['None or Unspecified', '23.5', nan, '13"', '26.5', '29.5', '14"',
       '20.5', '17.5"', '15.5"', '20.5"', '17.5', '7.0"', '15.5', '23.5"',
       '10"', '23.1"', '10 inch'], dtype=object)

In [21]:
df_use['Tire_Size'].replace(to_replace = ['None or Unspecified', '23.5', np.nan, '13"', '26.5', '29.5', '14"',
       '20.5', '17.5"', '15.5"', '20.5"', '17.5', '7.0"', '15.5', '23.5"',
       '10"', '23.1"', '10 inch'],
        value = [np.nan, 23.5, np.nan, 13,26.5,29.5,14,20.5,17.5,15.5,20.5,17.5,7,15.5,23.5,10,23.1,10], inplace =  True)

In [22]:
#Undercarriage_Pad_Width
df_use['Undercarriage_Pad_Width'].unique()

array([nan, 'None or Unspecified', '16 inch', '32 inch', '28 inch',
       '30 inch', '22 inch', '24 inch', '18 inch', '36 inch', '20 inch',
       '27 inch', '15 inch', '26 inch', '34 inch', '33 inch', '14 inch',
       '31 inch', '25 inch', '31.5 inch'], dtype=object)

In [23]:
#import re
df_use['Undercarriage_Pad_Width'] = [re.sub('inch','', str(x)) for x in df_use['Undercarriage_Pad_Width']]

In [26]:
df_use['Undercarriage_Pad_Width'].unique()

array([ nan, 16. , 32. , 28. , 30. , 22. , 24. , 18. , 36. , 20. , 27. ,
       15. , 26. , 34. , 33. , 14. , 31. , 25. , 31.5])

In [25]:
df_use['Undercarriage_Pad_Width'].replace(to_replace = ['None or Unspecified','nan'], value = [np.nan,np.nan], inplace = True)

In [27]:
df_use['Undercarriage_Pad_Width'].dtype

dtype('float64')

In [28]:
#Stick_Length
df_use['Stick_Length'].unique()

array([nan, 'None or Unspecified', '11\' 0"', '15\' 9"', '10\' 2"',
       '10\' 6"', '9\' 10"', '10\' 10"', '9\' 6"', '9\' 7"', '12\' 8"',
       '8\' 2"', '8\' 6"', '9\' 8"', '12\' 10"', '11\' 10"', '8\' 10"',
       '8\' 4"', '12\' 4"', '9\' 5"', '6\' 3"', '14\' 1"', '13\' 7"',
       '13\' 10"', '13\' 9"', '7\' 10"', '15\' 4"', '9\' 2"', '24\' 3"',
       '19\' 8"'], dtype=object)

In [29]:
df_use['Stick_Length'].replace('None or Unspecified',np.nan, inplace=  True)

In [30]:

def get_inches(val):
    for i in val['Stick_Length']:
        if i != np.nan:
            pattern = '([0-9]{1,2})(\' )([0-9]{1,2})(")'
            for item in re.finditer(pattern, str(i)):
                ft = item.group(1)
                inch = item.group(3)
                inches = int(float(ft)*12 + float(inch))
                val['Stick_Length'].replace(i,inches,inplace = True)

get_inches(df_use)
        
        
        

In [31]:
df_use['Stick_Length'].unique()

array([ nan, 132., 189., 122., 126., 118., 130., 114., 115., 152.,  98.,
       102., 116., 154., 142., 106., 100., 148., 113.,  75., 169., 163.,
       166., 165.,  94., 184., 110., 291., 236.])

In [32]:
df_use['Stick_Length'].dtype

dtype('float64')

In [33]:
#Thumb
df_use['Thumb'].unique()

array([nan, 'None or Unspecified', 'Hydraulic', 'Manual'], dtype=object)

In [34]:
pd.set_option('display.max_rows',None)

In [35]:
df_use.dtypes

SalesID                       int64
SalePrice                   float64
MachineID                     int64
ModelID                       int64
datasource                    int64
auctioneerID                float64
YearMade                      int64
MachineHoursCurrentMeter    float64
UsageBand                    object
fiModelDesc                  object
fiBaseModel                  object
fiSecondaryDesc              object
fiModelSeries                object
fiModelDescriptor            object
ProductSize                  object
fiProductClassDesc           object
state                        object
ProductGroup                 object
ProductGroupDesc             object
Drive_System                 object
Enclosure                    object
Forks                        object
Pad_Type                     object
Ride_Control                 object
Stick                        object
Transmission                 object
Turbocharged                 object
Blade_Extension             

In [36]:
#df_use.select_dtypes(include =['object'])
object_columns = [ i for i in df_use.columns.to_list() if df_use[i].dtype == object]

In [37]:
object_columns

['UsageBand',
 'fiModelDesc',
 'fiBaseModel',
 'fiSecondaryDesc',
 'fiModelSeries',
 'fiModelDescriptor',
 'ProductSize',
 'fiProductClassDesc',
 'state',
 'ProductGroup',
 'ProductGroupDesc',
 'Drive_System',
 'Enclosure',
 'Forks',
 'Pad_Type',
 'Ride_Control',
 'Stick',
 'Transmission',
 'Turbocharged',
 'Blade_Extension',
 'Enclosure_Type',
 'Engine_Horsepower',
 'Hydraulics',
 'Pushblock',
 'Ripper',
 'Scarifier',
 'Tip_Control',
 'Coupler',
 'Coupler_System',
 'Grouser_Tracks',
 'Hydraulics_Flow',
 'Track_Type',
 'Thumb',
 'Pattern_Changer',
 'Grouser_Type',
 'Backhoe_Mounting',
 'Blade_Type',
 'Travel_Controls',
 'Differential_Type',
 'Steering_Controls']

In [38]:
df_use['Tire_Size'].dtype == object

False

In [39]:
not_object_columns = [ i for i in df_use.columns.to_list() if df_use[i].dtype != object]

In [40]:
not_object_columns

['SalesID',
 'SalePrice',
 'MachineID',
 'ModelID',
 'datasource',
 'auctioneerID',
 'YearMade',
 'MachineHoursCurrentMeter',
 'Blade_Width',
 'Tire_Size',
 'Undercarriage_Pad_Width',
 'Stick_Length',
 'saleYear',
 'saleMonth',
 'saleWeek',
 'saleDay',
 'saleDayofweek',
 'saleDayofyear',
 'saleIs_month_end',
 'saleIs_month_start',
 'saleIs_quarter_end',
 'saleIs_quarter_start',
 'saleIs_year_end',
 'saleIs_year_start',
 'saleElapsed']

In [41]:
## fll na values
for i in not_object_columns:
    df_use[i].fillna(np.median(df_use[i]))

In [51]:
#df_use.isnull()

In [42]:
#train_cats(df_use)
df_use_new = pd.get_dummies(df_use, columns = object_columns)
df_use_new.head()

SalesID  SalePrice  MachineID  ModelID  datasource  auctioneerID  YearMade  \
0  1139246  11.097410     999089     3157         121           3.0      2004   
1  1139248  10.950807     117657       77         121           3.0      1996   
2  1139249   9.210340     434808     7009         121           3.0      2001   
3  1139251  10.558414    1026470      332         121           3.0      2001   
4  1139253   9.305651    1057373    17311         121           3.0      2007   

   MachineHoursCurrentMeter  Blade_Width  Tire_Size  Undercarriage_Pad_Width  \
0                      68.0           13        NaN                      NaN   
1                    4640.0           13       23.5                      NaN   
2                    2838.0           13        NaN                      NaN   
3                    3486.0           13        NaN                      NaN   
4                     722.0           13        NaN                      NaN   

   Stick_Length  saleYear  saleMonth  saleWeek  saleDay  saleDayofweek  \
0           NaN      2006         11        46       16              3   
1           NaN      2004          3        13       26              4   
2           NaN      2004          2         9       26              3   
3           NaN      2011          5        20       19              3   
4           NaN      2009          7        30       23              3   

   saleDayofyear  saleIs_month_end  saleIs_month_start  saleIs_quarter_end  \
0            320             False               False               False   
1             86             False               False               False   
2             57             False               False               False   
3            139             False               False               False   
4            204             False               False               False   

   saleIs_quarter_start  saleIs_year_end  saleIs_year_start   saleElapsed  \
0                 False            False              False  1.163635e+09   
1                 False            False              False  1.080259e+09   
2                 False            False              False  1.077754e+09   
3                 False            False              False  1.305763e+09   
4                 False            False              False  1.248307e+09   

   UsageBand_High  UsageBand_Low  UsageBand_Medium  fiModelDesc_100C  \
0               0              1                 0                 0   
1               0              1                 0                 0   
2               1              0                 0                 0   
3               1              0                 0                 0   
4               0              0                 1                 0   

   fiModelDesc_104  fiModelDesc_1066  fiModelDesc_1066E  fiModelDesc_1080  \
0                0                 0                  0                 0   
1                0                 0                  0                 0   
2                0                 0                  0                 0   
3                0                 0                  0                 0   
4                0                 0                  0                 0   

   fiModelDesc_1080B  fiModelDesc_1088  fiModelDesc_1088CK  \
0                  0                 0                   0   
1                  0                 0                   0   
2                  0                 0                   0   
3                  0                 0                   0   
4                  0                 0                   0   

   fiModelDesc_1088LT  fiModelDesc_1088TTL  fiModelDesc_10B  fiModelDesc_10C  \
0                   0                    0                0                0   
1                   0                    0                0                0   
2                   0                    0                0                0   
3                   0                    0                0          

In [44]:
df_use_new.shape

(401125, 7668)

In [55]:
df_use_new.dtypes

SalesID                                                                                  int64
SalePrice                                                                              float64
MachineID                                                                                int64
ModelID                                                                                  int64
datasource                                                                               int64
auctioneerID                                                                           float64
YearMade                                                                                 int64
MachineHoursCurrentMeter                                                               float64
Blade_Width                                                                              int64
Tire_Size                                                                              float64
Undercarriage_Pad_Width                           

In [26]:
x, y = df_use_new.drop(labels = ['SalePrice'], axis = 1), df_use_new['SalePrice']


In [28]:
x.head()

SalesID  MachineID  ModelID  datasource  auctioneerID  YearMade  \
0  1139246     999089     3157         121           3.0      2004   
1  1139248     117657       77         121           3.0      1996   
2  1139249     434808     7009         121           3.0      2001   
3  1139251    1026470      332         121           3.0      2001   
4  1139253    1057373    17311         121           3.0      2007   

   MachineHoursCurrentMeter  saleYear  saleMonth  saleWeek  saleDay  \
0                      68.0      2006         11        46       16   
1                    4640.0      2004          3        13       26   
2                    2838.0      2004          2         9       26   
3                    3486.0      2011          5        20       19   
4                     722.0      2009          7        30       23   

   saleDayofweek  saleDayofyear  saleIs_month_end  saleIs_month_start  \
0              3            320             False               False   
1              4             86             False               False   
2              3             57             False               False   
3              3            139             False               False   
4              3            204             False               False   

   saleIs_quarter_end  saleIs_quarter_start  saleIs_year_end  \
0               False                 False            False   
1               False                 False            False   
2               False                 False            False   
3               False                 False            False   
4               False                 False            False   

   saleIs_year_start   saleElapsed  UsageBand_High  UsageBand_Low  \
0              False  1.163635e+09               0              1   
1              False  1.080259e+09               0              1   
2              False  1.077754e+09               1              0   
3              False  1.305763e+09               1              0   
4              False  1.248307e+09               0              0   

   UsageBand_Medium  fiModelDesc_100C  fiModelDesc_104  fiModelDesc_1066  \
0                 0                 0                0                 0   
1                 0                 0                0                 0   
2                 0                 0                0                 0   
3                 0                 0                0                 0   
4                 1                 0                0                 0   

   fiModelDesc_1066E  fiModelDesc_1080  fiModelDesc_1080B  fiModelDesc_1088  \
0                  0                 0                  0                 0   
1                  0                 0                  0                 0   
2                  0                 0                  0                 0   
3                  0                 0                  0                 0   
4                  0                 0                  0                 0   

   fiModelDesc_1088CK  fiModelDesc_1088LT  fiModelDesc_1088TTL  \
0                   0                   0                    0   
1                   0                   0                    0   
2                   0                   0                    0   
3                   0                   0                    0   
4                   0                   0                    0   

   fiModelDesc_10B  fiModelDesc_10C  fiModelDesc_10DG  fiModelDesc_110  \
0                0                0                 0                0   
1                0                0                 0                0   
2                0                0                 0                0   
3                0                0                 0                0   
4                0                0                 0                0   

   fiModelDesc_1105  fiModelDesc_110S  fiModelDesc_110TLB  fiModelDesc_110Z  \
0                 0                 0                   0      

In [31]:
x.shape

(401125, 7734)

In [30]:
len(y)

401125

In [ ]:
m = RandomForestRegressor(n_jobs=-1)
m.fit(x, y)
m.score(x, y)

In [14]:
# function
import numpy as np
import pandas as pd
from fastai.imports import *
#from fastai.structured import *
from fastai.tabular.all import *
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
import re
import math
#print('Imported all the libs')
    
def get_inches(val):
    for i in val['Stick_Length']:
        if not pd.isna(i):
            pattern = '([0-9]{1,2})(\' )([0-9]{1,2})(")'
            for item in re.finditer(pattern, str(i)):
                ft = item.group(1)
                inch = item.group(3)
                inches = int(float(ft)*12 + float(inch))
                val['Stick_Length'].replace(i,inches,inplace = True)


def rmse(x,y):
    return math.sqrt(((x-y)**2).mean())


    
def mainf():
    #importlib()
    df = pd.read_csv('C:\\Users\\Naveen Kumar\\OneDrive - RxLogix\\Documents\\PersoMe\\MLcodes\\Bulldozers\\Train.csv',
                 low_memory = False, parse_dates =['saledate'])
    df_use = df.copy()
    df_use.SalePrice = np.log(df_use.SalePrice) # converting saleprice into log saleprice
    
    add_datepart(df_use, 'saledate') # formating saledate field
    
    # drop model columns
    df_use.drop(labels = ['fiModelDesc','fiBaseModel','fiSecondaryDesc','fiModelSeries','fiModelDescriptor','fiProductClassDesc'], 
            axis = 1, inplace = True)
    #print(df_use.dtypes)
    # handle blade width
    df_use['Blade_Width'].replace(to_replace = [np.nan, 'None or Unspecified', "12'", "14'", "13'", "16'", "<12'"],
                             value = [13, 13, 12, 14, 13, 16, 10], inplace =  True)
    
    # handle tiresize
    df_use['Tire_Size'].replace(to_replace = ['None or Unspecified', '23.5', np.nan, '13"', '26.5', '29.5', '14"',
       '20.5', '17.5"', '15.5"', '20.5"', '17.5', '7.0"', '15.5', '23.5"',
       '10"', '23.1"', '10 inch'],
        value = [pd.NA, 23.5, pd.NA, 13,26.5,29.5,14,20.5,17.5,15.5,20.5,17.5,7,15.5,23.5,10,23.1,10], inplace =  True)
    
    # handle Undercarriage_Pad_Width
    df_use['Undercarriage_Pad_Width'] = [re.sub('inch','', str(x)) for x in df_use['Undercarriage_Pad_Width']]
    df_use['Undercarriage_Pad_Width'].replace(to_replace = ['None or Unspecified','nan'], value = [pd.NA,pd.NA], 
                                              inplace = True)
    
    # handle Stick_Length
    df_use['Stick_Length'].replace('None or Unspecified',pd.NA, inplace=  True)
    #print('start')
    get_inches(df_use)
    #print('stop')
    
    # handle auctioneerID missing values
    #df_use['auctioneerID'].replace(np.nan,pd.NA, inplace =True)
    df_use['auctioneerID'].fillna(0, inplace =True)
    
    # handle MachineHoursCurrentMeter
    #df_use['MachineHoursCurrentMeter'].replace(np.nan,pd.NA, inplace =True)
    df_use['MachineHoursCurrentMeter'].fillna(0, inplace =True)
    
    
    
    '''for i in df_use.columns:
        if df_use[i].isnull().values.any():
            print(i)
            print(df_use[i].dtype) '''
    ##
    object_columns = [ i for i in df_use.columns.to_list() if df_use[i].dtype == object]
    not_object_columns = [ i for i in df_use.columns.to_list() if df_use[i].dtype != object]
    #print(not_object_columns)
    
    ## fll na values
    for i in not_object_columns:
        #df_use[i].fillna(np.median(df_use[i]), inplace = True)
        df_use[i].fillna(df_use[i].median(), inplace = True)
        
    #print(df_use.dtypes)
    ###
    df_use_new = pd.get_dummies(df_use, columns = object_columns)
    print(df_use_new.shape)
    
    # Going for model
    lim = int(len(df_use_new)*(0.95))
    df_use_new_train = df_use_new.iloc[:lim,:]
    df_use_new_val = df_use_new.iloc[lim:,:]
    
    df_use_new_rand_train = df_use_new_train.sample(n = 40000)
    
    #x, y = df_use_new.drop(labels = ['SalePrice'], axis = 1), df_use_new['SalePrice']
    x_train, y_train = df_use_new_rand_train.drop(labels = ['SalePrice'], axis = 1), df_use_new_rand_train['SalePrice']
    x_val, y_val = df_use_new_val.drop(labels = ['SalePrice'], axis = 1), df_use_new_val['SalePrice']
    
    #
    #lim = int(len(y)*(0.95))
    
    #x_train_large, y_train_large = x.iloc[:lim,:], y.iloc[:lim]
    #x_val, y_val = x.iloc[lim:,:], y.iloc[lim:]
    
    #print(x.isnull().values.any())
    #print(x.isnull().sum().sum())
    pd.set_option('display.max_columns',None)
    pd.set_option('display.max_rows',None)
    #print(x.head())
    '''for i in x.columns:
        if x[i].isnull().values.any():
            print(i)
            print(x[i].dtype)'''
        
    
    m = RandomForestRegressor(n_jobs=-1)
    
    %time m.fit(x_train, y_train)
    print(m.score(x_val, y_val))
    print(rmse(m.predict(x_val),y_val))
    
mainf()
    
    

c:\users\naveen kumar\appdata\local\programs\python\python39\lib\site-packages\pandas\core\missing.py:56: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  mask |= arr == x


(401125, 263)
Wall time: 24.9 s
0.8003232136684515
0.33059577937706214


In [42]:
import numpy as np
import pandas as pd
from fastai.imports import *
#from fastai.structured import *
from fastai.tabular.all import *
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
import re
import math
#print('Imported all the libs')

In [43]:
def get_inches_old(val):
    for i in val['Stick_Length']:
        if not pd.isna(i):
            pattern = '([0-9]{1,2})(\' )([0-9]{1,2})(")'
            for item in re.finditer(pattern, str(i)):
                ft = item.group(1)
                inch = item.group(3)
                inches = int(float(ft)*12 + float(inch))
                val['Stick_Length'].replace(i,inches,inplace = True)

In [74]:
def get_inches(val):
    ser = pd.Series(val['Stick_Length'])
    #print(ser.isna().sum())
    
    for i in range(len(ser)):
        if not pd.isna(ser.iloc[i]):
            pattern = '([0-9]{1,2})(\' )([0-9]{1,2})(")'
            for item in re.finditer(pattern, str(ser.iloc[i])):
                ft = item.group(1)
                inch = item.group(3)
                inches = int(float(ft)*12 + float(inch))
                ser.iloc[i] = inches
                #ser.replace(ser.iloc[i],inches,inplace = True)
    val.drop(columns =  ['Stick_Length'])
    #print(ser.isna().sum())
    val['Stick_Length']  = ser
    return val

In [44]:
def rmse(x,y):
    return math.sqrt(((x-y)**2).mean())

In [76]:
df = pd.read_csv('C:\\Users\\Naveen Kumar\\OneDrive - RxLogix\\Documents\\PersoMe\\MLcodes\\Bulldozers\\Train.csv',
                 low_memory = False, parse_dates =['saledate'])
df_use = df.copy()
df_use.SalePrice = np.log(df_use.SalePrice) # converting saleprice into log saleprice
#print('1')
add_datepart(df_use, 'saledate') # formating saledate field

# drop model columns
df_use.drop(labels = ['fiModelDesc','fiBaseModel','fiSecondaryDesc','fiModelSeries','fiModelDescriptor','fiProductClassDesc'], 
        axis = 1, inplace = True)
#print(df_use.dtypes)
# handle blade width
#print('2')
df_use['Blade_Width'].replace(to_replace = [np.nan, 'None or Unspecified', "12'", "14'", "13'", "16'", "<12'"],
                         value = [13, 13, 12, 14, 13, 16, 10], inplace =  True)
#print('3')
# handle tiresize
df_use['Tire_Size'].replace(to_replace = ['None or Unspecified', '23.5', np.nan, '13"', '26.5', '29.5', '14"',
   '20.5', '17.5"', '15.5"', '20.5"', '17.5', '7.0"', '15.5', '23.5"',
   '10"', '23.1"', '10 inch'],
    value = [pd.NA, 23.5, pd.NA, 13,26.5,29.5,14,20.5,17.5,15.5,20.5,17.5,7,15.5,23.5,10,23.1,10], inplace =  True)
#print('4')
# handle Undercarriage_Pad_Width
df_use['Undercarriage_Pad_Width'] = [re.sub('inch','', str(x)) for x in df_use['Undercarriage_Pad_Width']]
df_use['Undercarriage_Pad_Width'].replace(to_replace = ['None or Unspecified','nan'], value = [pd.NA,pd.NA], 
                                          inplace = True)
#print('5')
# handle Stick_Length
df_use['Stick_Length'].replace('None or Unspecified',pd.NA, inplace=  True)
#print('5.1')
#print('start')
get_inches(df_use)
#print('stop')
#print('6')
# handle auctioneerID missing values
#df_use['auctioneerID'].replace(np.nan,pd.NA, inplace =True)
df_use['auctioneerID'].fillna(0, inplace =True)

# handle MachineHoursCurrentMeter
#df_use['MachineHoursCurrentMeter'].replace(np.nan,pd.NA, inplace =True)
df_use['MachineHoursCurrentMeter'].fillna(0, inplace =True)

#print('7')

'''for i in df_use.columns:
    if df_use[i].isnull().values.any():
        print(i)
        print(df_use[i].dtype) '''
##
object_columns = [ i for i in df_use.columns.to_list() if df_use[i].dtype == object]
not_object_columns = [ i for i in df_use.columns.to_list() if df_use[i].dtype != object]
#print(not_object_columns)
#print('8')
## fll na values
for i in not_object_columns:
    #df_use[i].fillna(np.median(df_use[i]), inplace = True)
    df_use[i].fillna(df_use[i].median(), inplace = True)
#print('9')
#print(df_use.dtypes)
###
df_use_new = pd.get_dummies(df_use, columns = object_columns)
print(df_use_new.shape)




(401125, 263)


In [77]:
# Going for model
lim = int(len(df_use_new)*(0.95))
df_use_new_train = df_use_new.iloc[:lim,:]
df_use_new_val = df_use_new.iloc[lim:,:]
x_val, y_val = df_use_new_val.drop(labels = ['SalePrice'], axis = 1), df_use_new_val['SalePrice']


In [80]:
df_use_new_rand_train = df_use_new_train.sample(n = 100000)

#x, y = df_use_new.drop(labels = ['SalePrice'], axis = 1), df_use_new['SalePrice']
x_train, y_train = df_use_new_rand_train.drop(labels = ['SalePrice'], axis = 1), df_use_new_rand_train['SalePrice']




In [81]:
m = RandomForestRegressor(n_estimators=20, n_jobs=-1, min_samples_leaf = 1) #oob_score = True)
    
%time m.fit(x_train, y_train)
print('Training set score :',m.score(x_train, y_train))
print('Training set rmse :',rmse(m.predict(x_train),y_train))
print('Validation set score :',m.score(x_val, y_val))
print('Validation set rmse :',rmse(m.predict(x_val),y_val))

Wall time: 15.1 s
Training set score : 0.9788074538495032
Training set rmse : 0.10028062842259733
Validation set score : 0.8043604474432098
Validation set rmse : 0.3272365806619516
